In [1]:
# python -m sample.generate --model_path ./save/unet_adazero_xl_x0_abs_proj10_fp16_clipwd_224/model000500000.pt --text_prompt "a person is walking while raising both hands" --guidance_mode kps

In [2]:
import sys
sys.path.append('../')
import os
os.chdir('../')
%reload_ext autoreload
%autoreload 2
import matplotlib.pyplot as plt
%matplotlib notebook
%matplotlib inline
os.environ["CUDA_VISIBLE_DEVICES"]="3"

In [3]:
from functools import partial
from pprint import pprint
from utils.fixseed import fixseed
import os
import time
import numpy as np
import torch
import copy
import json
from utils.parser_util import generate_args
from utils.model_util import create_model_and_diffusion, load_saved_model
from utils.output_util import sample_to_motion, construct_template_variables, save_multiple_samples
from utils.generation_template import get_template
from utils import dist_util
from model.cfg_sampler import ClassifierFreeSampleModel
from data_loaders.get_data import DatasetConfig, get_dataset_loader
from data_loaders.humanml.scripts.motion_process import recover_from_ric
import data_loaders.humanml.utils.paramUtil as paramUtil
from data_loaders import humanml_utils
from data_loaders.humanml.utils.plot_script import plot_3d_motion
import shutil
from data_loaders.tensors import collate
# import flag
from torch.cuda import amp
from sample.condition import (get_target_from_kframes, get_inpainting_motion_from_traj, 
                              get_target_and_inpt_from_kframes_batch, 
                              cond_fn_key_location, cond_fn_sdf, log_trajectory_from_xstart,
                              CondKeyLocations, CondKeyLocationsWithSdf)

from sample.keyframe_pattern import get_kframes, get_obstacles

from sample.generate import load_dataset, load_traj_model, load_processed_file

/home/epinyoan/miniconda3/envs/gmd/lib/python3.7/site-packages/tqdm/auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [4]:
sys.argv = ['/home/epinyoan/git/guided-motion-diffusion/sample/generate.py',
            '--model_path', './save/unet_adazero_xl_x0_abs_proj10_fp16_clipwd_224/model000500000.pt',
             '--text_prompt', "a person is walking while raising both hands",
             '--guidance_mode', 'kps']
args = generate_args()
args = get_template(args, template_name=args.guidance_mode)
fixseed(args.seed)

In [5]:
max_frames = 196 if args.dataset in ['kit', 'humanml'] else 60
fps = 12.5 if args.dataset == 'kit' else 20
n_frames = min(max_frames, int(args.motion_length * fps))
cut_frames = int(args.motion_length_cut * fps)
is_using_data = not any([
    args.input_text, args.text_prompt, args.action_file, args.action_name
])
dist_util.setup_dist(args.device)

In [6]:
texts = [args.text_prompt]
args.num_samples = 3
args.num_repetitions = 1
args.batch_size = args.num_samples
data = load_dataset(args, max_frames, n_frames)
total_num_samples = args.num_samples * args.num_repetitions
model, diffusion = create_model_and_diffusion(args, data)
load_saved_model(model, args.model_path)
model = ClassifierFreeSampleModel(
        model)  # wrapping model with the classifier-free sampler
model.to(dist_util.dev())
model.eval()  

collate_args = [{
    'inp': torch.zeros(n_frames),
    'tokens': None,
    # this would be incorrect for UNET models
    # 'lengths': n_frames,
    'lengths': cut_frames,
}] * args.num_samples
# model_kwargs['y']['lengths']
is_t2m = any([args.input_text, args.text_prompt])
collate_args = [
    dict(arg, text=txt) for arg, txt in zip(collate_args, texts)
]
_, model_kwargs = collate(collate_args)
model_kwargs['y']['traj_model'] = args.traj_only

traj_model, traj_diffusion = load_traj_model(data)
traj_model_kwargs = copy.deepcopy(model_kwargs)
traj_model_kwargs['y']['traj_model'] = True

all_motions = []
all_lengths = []
all_text = []
obs_list = []
USE_CLASSIFIER_FREE = False # True
model_device = next(model.parameters()).device

Reading ././dataset/humanml_opt.txt
Loading dataset t2m ...
proj_matrix_dir = ./dataset
mode = text_only
t2m dataset aug: none std_scale_shift: (1.0, 0.0)
t2m dataset drop redundant information: False


  0%|          | 0/4384 [00:00<?, ?it/s]

100%|██████████| 4384/4384 [00:00<00:00, 22576.66it/s]


Using UNET with lantent dim:  512  and mults:  [2, 2, 2, 2]
dims:  [263, 1024, 1024, 1024, 1024] mults:  [2, 2, 2, 2]
[ models/temporal ] Channel dimensions: [(263, 1024), (1024, 1024), (1024, 1024), (1024, 1024)]
EMBED TEXT
Loading CLIP...
loading avg model
Setting traj model ...
 - model_path is given in the function call. Cmd path, if any, will be ignored.
Using UNET with lantent dim:  512  and mults:  [0.125, 0.25, 0.5]
dims:  [4, 64, 128, 256] mults:  [0.125, 0.25, 0.5]
[ models/temporal ] Channel dimensions: [(4, 64), (64, 128), (128, 256)]
EMBED TEXT
Loading CLIP...
Loading traj model checkpoints from [./save/traj_unet_adazero_swxs_eps_abs_fp16_clipwd_224/model000062500.pt]...
loading avg model


In [7]:
# this is the pre process position
input_motions, ground_positions = load_processed_file(model_device, args.batch_size, args.traj_only)
input_skels = recover_from_ric(input_motions.permute(0, 2, 3, 1), 22, abs_3d=False)
input_skels = input_skels.squeeze(1)
kframes = get_kframes(pattern="zigzag")
motion_cond_until = 20
motion_impute_until = 1

In [8]:
kframes_num = [a for (a,b) in kframes] # [0, 30, 60, 90, 119]
kframes_posi = torch.tensor(kframes_num, dtype=torch.int).unsqueeze(0).repeat(args.batch_size, 1)
dummy_skel_motions = torch.zeros([1, 22, 3, n_frames])
for (tt, locs) in kframes:
    print("target at %d = %.1f, %.1f" % (tt, locs[0], locs[1]))
    dummy_skel_motions[0, 0, [0, 2], tt] = torch.tensor([locs[0], locs[1]])
dummy_skel_motions = dummy_skel_motions.repeat(args.batch_size, 1, 1, 1)  # [1, 22, 3, max_length]

(target, target_mask, 
    inpaint_traj_p2p, inpaint_traj_mask_p2p,
    inpaint_traj_points, inpaint_traj_mask_points,
    inpaint_motion_p2p, inpaint_mask_p2p,
    inpaint_motion_points, inpaint_mask_points) = get_target_and_inpt_from_kframes_batch(dummy_skel_motions, kframes_posi, data.dataset)
target = target.to(model_device)
target_mask = target_mask.to(model_device)
model_kwargs['y']['target'] = target
model_kwargs['y']['target_mask'] = target_mask

target at 1 = 0.0, 0.0
target at 40 = 0.0, 2.0
target at 79 = 2.0, 2.0
target at 116 = 2.0, 4.0


In [9]:
model_kwargs['y']['scale'] = torch.ones(args.batch_size, device=dist_util.dev()) * args.guidance_param
traj_model_kwargs['y']['scale'] = torch.ones(
    args.batch_size,
    device=dist_util.dev()) * args.guidance_param
impute_slack = 20
impute_until = 100
traj_model_kwargs['y']['inpainted_motion'] = inpaint_traj_p2p.to(model_device)
traj_model_kwargs['y']['inpainting_mask'] = inpaint_traj_mask_p2p.to(model_device)

traj_model_kwargs['y']['cond_until'] = impute_slack
traj_model_kwargs['y']['impute_until'] = impute_until
# NOTE: We have the option of switching the target motion from line to just key locations
# We call this a 'second stage', which will start after t reach 'impute_until'
traj_model_kwargs['y']['impute_until_second_stage'] = impute_slack
traj_model_kwargs['y']['inpainted_motion_second_stage'] = inpaint_traj_points.to(model_device)
traj_model_kwargs['y']['inpainting_mask_second_stage'] = inpaint_traj_mask_points.to(model_device)

traj_diffusion.data_transform_fn = None
traj_diffusion.data_inv_transform_fn = None
traj_diffusion.log_trajectory_fn = None

In [10]:
cond_fn_traj = CondKeyLocations(target=target,
    target_mask=target_mask,
    transform=data.dataset.t2m_dataset.transform_th,
    inv_transform=data.dataset.t2m_dataset.inv_transform_th,
    abs_3d=args.abs_3d,
    classifiler_scale=args.classifier_scale,
    use_mse_loss=args.gen_mse_loss,
    use_rand_projection=False,
    )

sample_fn = traj_diffusion.p_sample_loop
dump_steps = [1, 100, 300, 500, 700, 850, 999]
traj_sample = sample_fn(
    traj_model,
    (args.batch_size, traj_model.njoints, traj_model.nfeats,
        n_frames),
    clip_denoised=True,  # False,
    model_kwargs=traj_model_kwargs,
    skip_timesteps=0,  # 0 is the default value - i.e. don't skip any step
    init_image=None, # None,
    progress=True,
    dump_steps=dump_steps,  # None,
    noise=None,
    const_noise=False,
    cond_fn=cond_fn_traj,
)

# Set inpainting information for motion model
traj_motion, traj_mask = get_inpainting_motion_from_traj(
    traj_sample[-1],
    inv_transform_fn=data.dataset.t2m_dataset.inv_transform_th,
)
# plt.scatter(traj_motion[0, 1, 0, :120].cpu().numpy(), traj_motion[0, 2, 0, :120].cpu().numpy())
model_kwargs['y']['inpainted_motion'] = traj_motion
model_kwargs['y']['inpainting_mask'] = traj_mask
# Assume the target has dimention [bs, 120, 22, 3] in case we do key poses instead of key location
target = torch.zeros([args.batch_size, n_frames, 22, 3], device=traj_motion.device)
target_mask = torch.zeros_like(target, dtype=torch.bool)
# This assume that the traj_motion is in the 3D space without normalization
# traj_motion: [3, 263, 1, 196]
target[:, :, 0, [0, 2]] = traj_motion.permute(0, 3, 2, 1)[:, :, 0,[1, 2]]
# target_mask[:, :int(flag.GEN_MOTION_LENGTH_CUT * 20.0), 0, [0, 2]] = True
target_mask[:, :, 0, [0, 2]] = True

  0%|          | 0/1000 [00:00<?, ?it/s]

100%|██████████| 1000/1000 [01:21<00:00, 12.28it/s]


In [11]:
sample_fn = diffusion.p_sample_loop
dump_steps = [999]
args.do_inpaint

True

In [12]:
model_kwargs['y']['cond_until'] = motion_cond_until  # impute_slack
model_kwargs['y']['impute_until'] = motion_impute_until # 20  # impute_slack
# Pass functions to the diffusion
diffusion.data_get_mean_fn = data.dataset.t2m_dataset.get_std_mean
diffusion.data_transform_fn = data.dataset.t2m_dataset.transform_th
diffusion.data_inv_transform_fn = data.dataset.t2m_dataset.inv_transform_th

In [13]:
cond_fn = CondKeyLocations(target=target,
    target_mask=target_mask,
    transform=data.dataset.t2m_dataset.transform_th,
    inv_transform=data.dataset.t2m_dataset.inv_transform_th,
    abs_3d=args.abs_3d,
    classifiler_scale=args.classifier_scale,
    use_mse_loss=args.gen_mse_loss,
    use_rand_projection=args.use_random_proj
    )
sample = sample_fn(
    model,
    (args.batch_size, model.njoints, model.nfeats, n_frames),
    # clip_denoised=False,
    clip_denoised=not args.predict_xstart,
    model_kwargs=model_kwargs,
    skip_timesteps=0,  # 0 is the default value - i.e. don't skip any step # NOTE: testing this
    init_image=None, # input_motions,  # init_image, # None, # NOTE: testing this
    progress=True,
    dump_steps=dump_steps,  # None,
    noise=None,
    const_noise=False,
    cond_fn=cond_fn,
)

  0%|          | 0/1000 [00:00<?, ?it/s]

100%|██████████| 1000/1000 [01:43<00:00,  9.69it/s]


In [14]:
gen_eff_len = min(sample[0].shape[-1], cut_frames)
print('cut the motion length to', gen_eff_len)
for j in range(len(sample)):
    sample[j] = sample[j][:, :, :, :gen_eff_len]
###################

num_dump_step = len(dump_steps)
args.num_dump_step = num_dump_step
# Convert sample to XYZ skeleton locations
# Each return size [bs, 1, 3, 120]
cur_motions, cur_lengths, cur_texts = sample_to_motion(
    sample, args, model_kwargs, model, gen_eff_len,
    data.dataset.t2m_dataset.inv_transform)

cut the motion length to 120
created 3 samples


### Render

In [50]:
traj_sample[-1].shape

torch.Size([3, 4, 1, 196])

In [46]:
# debug this one from "/home/epinyoan/git/guided-motion-diffusion/sample/condition.py log_trajectory_from_xstart"
x_in_pose_space = data.dataset.t2m_dataset.inv_transform_th(
        traj_sample[-1].permute(0, 2, 3, 1),
        use_rand_proj=False,
        traject_only=True)
n_joints = 22
x_in_joints = recover_from_ric(x_in_pose_space, n_joints,
                                abs_3d=True)  # [bs, 1, 120, 22, 3]
trajec = x_in_joints[:, 0, :, 0, :].detach().cpu().numpy()  # [bs, 120, 3]
trajec.shape

(3, 196, 3)

In [34]:
pose = cur_motions[0][0].transpose(2,0,1)
pose.shape

(120, 22, 3)

In [47]:
from exit.utils import animate3d, t2m_bone
animate3d(pose, BONE_LINK=t2m_bone, first_total_standard=63, root_path=trajec[0], axis_visible=True)